In [102]:
import pandas as pd
import numpy as np
import xgboost as xgb
import matplotlib as plt
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report, roc_auc_score, make_scorer, balanced_accuracy_score, ConfusionMatrixDisplay
from sklearn.model_selection import train_test_split, GridSearchCV, RandomizedSearchCV
from ucimlrepo import fetch_ucirepo 
from sklearn.utils import class_weight
from imblearn.over_sampling import SMOTE
from imblearn.pipeline import Pipeline as ImbPipeline
from sklearn.metrics import precision_recall_fscore_support
from scipy.stats import randint, uniform
from xgboost import XGBClassifier
from sklearn.multiclass import OneVsOneClassifier

# fetch dataset 
# predict_students_dropout_and_academic_success = fetch_ucirepo(id=697) 
# variable information 
# print(predict_students_dropout_and_academic_success.variables) 

In [103]:
df=pd.read_csv('Resources/data.csv',delimiter=';')
df['Target'] = pd.Categorical(df['Target'])
df['Target'] = df['Target'].cat.codes
print(df['Target'].value_counts())
df.head()

Target
2    2209
0    1421
1     794
Name: count, dtype: int64


Marital status  Application mode  Application order  Course  \
0               1                17                  5     171   
1               1                15                  1    9254   
2               1                 1                  5    9070   
3               1                17                  2    9773   
4               2                39                  1    8014   

   Daytime/evening attendance\t  Previous qualification  \
0                             1                       1   
1                             1                       1   
2                             1                       1   
3                             1                       1   
4                             0                       1   

   Previous qualification (grade)  Nacionality  Mother's qualification  \
0                           122.0            1                      19   
1                           160.0            1                       1   
2                           122.0            1                      37   
3                           122.0            1                      38   
4                           100.0            1                      37   

   Father's qualification  ...  Curricular units 2nd sem (credited)  \
0                      12  ...                                    0   
1                       3  ...                                    0   
2                      37  ...                                    0   
3                      37  ...                                    0   
4                      38  ...                                    0   

   Curricular units 2nd sem (enrolled)  \
0                                    0   
1                                    6   
2                                    6   
3                                    6   
4                                    6   

   Curricular units 2nd sem (evaluations)  \
0                                       0   
1                                       6   
2                                       0   
3                                      10   
4                                       6   

   Curricular units 2nd sem (approved)  Curricular units 2nd sem (grade)  \
0                                    0                          0.000000   
1                                    6                         13.666667   
2                                    0                          0.000000   
3                                    5                         12.400000   
4                                    6                         13.000000   

   Curricular units 2nd sem (without evaluations)  Unemployment rate  \
0                                               0               10.8   
1                                               0               13.9   
2                                               0               10.8   
3                                               0                9.4   
4                                               0               13.9   

   Inflation rate   GDP  Target  
0             1.4  1.74       0  
1            -0.3  0.79       2  
2             1.4  1.74       0  
3            -0.8 -3.12       2  
4            -0.3  0.79       2  

[5 rows x 37 columns]

In [104]:
categorical_df=df.drop(columns=['GDP', 'Inflation rate', 'Unemployment rate', 'Admission grade', 'Previous qualification (grade)','Target'])
categorical_columns=list(categorical_df.columns)

In [105]:
y=df['Target']
X=df.drop(columns='Target')

In [106]:
X=pd.get_dummies(X,columns=categorical_columns).astype(int)

In [107]:
X_train,X_test,y_train,y_test=train_test_split(X,y,random_state=1,test_size=0.2, stratify=y)

# Define the SMOTE method
smote = SMOTE()

# Create the resampled feature set
X_resampled, y_resampled = smote.fit_resample(X_train, y_train)

# Convert your data to DMatrix format
dtrain = xgb.DMatrix(X_resampled, label=y_resampled, nthread=-1)
dtest = xgb.DMatrix(X_test, label=y_test, nthread=-1)


In [108]:
from xgboost import XGBClassifier
from sklearn.multiclass import OneVsOneClassifier

# Initialize your XGBoost model
# base_params = {
#     'tree_method': 'hist',
#     'eval_metric': 'aucpr',
#     'objective': 'binary:logistic',  # For binary classification in OvO
#     'random_state': 1,
#     'device': 'cuda'  # Change to 'cuda' if using GPU
# }
base_params= {'eval_metric': 'aucpr', 'objective': 'binary:logistic', 'random_state': 1, 'device': 'cpu'}
xgb_model = XGBClassifier(**base_params)

# Create an OvO classifier using XGBoost
ovo_xgb = OneVsOneClassifier(xgb_model)
# Train the OvO classifier
ovo_xgb.fit(X_resampled, y_resampled)

# Make predictions
predictions = ovo_xgb.predict(X_test)

In [109]:
predictions=ovo_xgb.predict(X_test)
confusion_matrix(y_test, predictions)
print(classification_report(y_test, predictions))
print("Accuracy: ", accuracy_score(y_test, predictions))

              precision    recall  f1-score   support

           0       0.84      0.73      0.78       284
           1       0.53      0.45      0.48       159
           2       0.79      0.90      0.84       442

    accuracy                           0.76       885
   macro avg       0.72      0.69      0.70       885
weighted avg       0.76      0.76      0.76       885

Accuracy:  0.7649717514124293


In [110]:
ovo_xgb.estimators_[0]

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device='cpu', early_stopping_rounds=None,
              enable_categorical=False, eval_metric='aucpr', feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None,
              num_parallel_tree=None, random_state=1, ...)

In [111]:
def weight_optimizer(weight_combinations,best_params = {},best_weights = None,best_f1_score=0):
    for weights in weight_combinations:
        weight = class_weight.compute_sample_weight(weights, y=y_resampled)

        # Train the model
        best_params['eval_metric']= 'aucpr'
        best_params['early_stopping_rounds']=20
        best_params['objective']= 'binary:logistic'
        best_params['random_state']= 1
        model = XGBClassifier(**best_params)
        model.fit(X_resampled, y_resampled,sample_weight=weight,verbose=True,eval_set=[(X_test,y_test)])

        # Convert probabilities to class labels
        predict = model.predict(X_test)
        # Get the precision, recall, f1-score, and support
        precision, recall, f1_score, support = precision_recall_fscore_support(y_test, predict)

        # Find the index of the smallest f1 score
        min_index = f1_score.argmin()

        if f1_score[min_index]>best_f1_score:
            best_weights=weights
            best_f1_score=f1_score[min_index]
            best_f1_score
            best_report=classification_report(y_test, predict)
    print(best_f1_score)
    print(best_weights)
    print(best_report)
    return best_weights

In [112]:
def hyperparameter_optimizer(estimator,param_grid,scoring,n_jobs=-1,cv=3,verbose=2,sample_weight=None,n_iter=180):
    weights = class_weight.compute_sample_weight(sample_weight, y=y_resampled)
    rand_search=RandomizedSearchCV(estimator=estimator, param_distributions=param_grid, scoring=scoring, n_jobs=n_jobs, cv=cv, verbose=verbose,n_iter=n_iter)
    rand_search.fit(X_resampled,y_resampled,sample_weight=weights)
    best_params = rand_search.best_params_
    return best_params

In [113]:
def model_rating(params,ranking=None,weights={0:1,1:1,2:1}):    
    if ranking!=None:
        id=sorted(ranking, key=lambda x: x['id'], reverse=True)[0]['id']+1
    if ranking==None:
        ranking=[]
        id=1
    weight = class_weight.compute_sample_weight(weights, y=y_resampled)   
    params['eval_metric']= 'aucpr'
    params['early_stopping_rounds']=20
    params['objective']= 'binary:logistic'
    params['random_state']= 1
    model = XGBClassifier(**params)
    model.fit(X_resampled,y_resampled,sample_weight=weight,verbose=True, eval_set=[(X_test,y_test)])
    predict = model.predict(X_test)
    
    # Get the precision, recall, f1-score, and support
    precision, recall, f1_score, support = precision_recall_fscore_support(y_test, predict)

    # Find the index of the smallest f1 score
    min_f1 = f1_score.argmin()
    min_recall = recall.argmin()
    min_precision = precision.argmin()
    full_report=classification_report(y_test, predict)
    entry= {'id':id,'weights':weights,'parameters':params,'f1':f1_score[min_f1],'recall':recall[min_recall],'precision':precision[min_precision],'full_report':full_report}
    ranking.append(entry)
    best_f1_score = sorted(ranking, key=lambda x: x['f1'], reverse=True)
    best_recall = sorted(ranking, key=lambda x: x['recall'], reverse=True)
    best_precision = sorted(ranking, key=lambda x: x['precision'], reverse=True)
    print('The best f1: ',best_f1_score[0])
    print('The best recall: ',best_recall[0])    
    print('The best precision: ',best_precision[0])  
    return ranking, best_f1_score[0]['f1'], best_recall[0]['recall'], best_precision[0]['precision']

In [114]:
params = {'gamma': uniform(0,.5), 'learning_rate': uniform(.1,.2), 'max_depth': randint(3,7), 'reg_lambda': randint(1,10), 'subsample': uniform(.2,.7)}

In [115]:
from itertools import combinations
import numpy as np

def generate_class_pairs(y):
    """ Generate all unique pairs of class labels. """
    unique_classes = np.unique(y)
    return list(combinations(unique_classes, 2))

def create_binary_dataset(X, y, class_pair):
    """ Create a subset of the dataset for a given pair of classes. """
    mask = np.isin(y, class_pair)
    X_binary = X[mask]
    y_binary = y[mask]

    # Relabel the classes as 0 and 1
    y_binary = np.where(y_binary == class_pair[0], 0, 1)
    return X_binary, y_binary

# Generate binary datasets for each class pair and store in a list of dictionaries
class_pairs = generate_class_pairs(y_train)
binary_datasets = []

for pair in class_pairs:
    X_binary, y_binary = create_binary_dataset(X_train, y_train, pair)
    binary_datasets.append({
        'pair': pair,
        'X_binary': X_binary,
        'y_binary': y_binary
    })

In [116]:
X=binary_datasets[0]['X_binary']
y=binary_datasets[0]['y_binary']
X_train,X_test,y_train,y_test=train_test_split(X,y,random_state=1,test_size=0.2, stratify=y)

# Assuming y_train contains your training labels
unique_classes, counts = np.unique(y_train, return_counts=True)
class_counts = dict(zip(unique_classes, counts))

# Calculate the ratio
# For a binary classification (class 0 and class 1 for example)
if len(class_counts) == 2:
    ratio = max(counts) / min(counts)
    print("Class Imbalance Ratio:", ratio)
else:
    print("Class counts:", class_counts)
# Define the SMOTE method
smote = SMOTE()

# Create the resampled feature set
X_resampled, y_resampled = smote.fit_resample(X_train, y_train)

Class Imbalance Ratio: 1.7893700787401574


In [117]:
base_params= {'eval_metric': 'aucpr', 'objective': 'binary:logistic', 'random_state': 1, 'device': 'cpu'}
xgb_bin_0_1=XGBClassifier(**base_params)
xgb_bin_0_1.fit(X_resampled,y_resampled,verbose=True,eval_set=[(X_test,y_test)])

[0]	validation_0-aucpr:0.65179
[1]	validation_0-aucpr:0.61904
[2]	validation_0-aucpr:0.61235
[3]	validation_0-aucpr:0.64886
[4]	validation_0-aucpr:0.65507
[5]	validation_0-aucpr:0.65248
[6]	validation_0-aucpr:0.66985
[7]	validation_0-aucpr:0.67204
[8]	validation_0-aucpr:0.69119
[9]	validation_0-aucpr:0.68710
[10]	validation_0-aucpr:0.68693
[11]	validation_0-aucpr:0.69994
[12]	validation_0-aucpr:0.69564
[13]	validation_0-aucpr:0.67702
[14]	validation_0-aucpr:0.67727
[15]	validation_0-aucpr:0.68033
[16]	validation_0-aucpr:0.68641
[17]	validation_0-aucpr:0.68902
[18]	validation_0-aucpr:0.69633
[19]	validation_0-aucpr:0.69190
[20]	validation_0-aucpr:0.69072
[21]	validation_0-aucpr:0.69550
[22]	validation_0-aucpr:0.69749
[23]	validation_0-aucpr:0.69582
[24]	validation_0-aucpr:0.70123
[25]	validation_0-aucpr:0.69637
[26]	validation_0-aucpr:0.69602
[27]	validation_0-aucpr:0.69694
[28]	validation_0-aucpr:0.70348
[29]	validation_0-aucpr:0.70484
[30]	validation_0-aucpr:0.70279
[31]	validation_0-

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device='cpu', early_stopping_rounds=None,
              enable_categorical=False, eval_metric='aucpr', feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None,
              num_parallel_tree=None, random_state=1, ...)

In [118]:

predict=xgb_bin_0_1.predict(X_test)
confusion_matrix(y_test, predict)
print(classification_report(y_test, predict))
print("Accuracy: ", accuracy_score(y_test, predict))

              precision    recall  f1-score   support

           0       0.85      0.78      0.81       228
           1       0.66      0.76      0.70       127

    accuracy                           0.77       355
   macro avg       0.75      0.77      0.76       355
weighted avg       0.78      0.77      0.77       355

Accuracy:  0.7718309859154929


In [119]:
weight_options = {
    'class_0': [.2,.3,.4,.5,.6,.7,.8,.9,1,1.1,1.2,1.3,1.4,1.5,1.6,1.7,1.8,1.9,2],
    'class_1': [.2,.3,.4,.5,.6,.7,.8,.9,1,1.1,1.2,1.3,1.4,1.5,1.6,1.7,1.8,1.9,2],
}
ratios=[]
weight_combinations=[]
for w0 in weight_options['class_0']:
    for w1 in weight_options['class_1']:
        if w0/w1 not in ratios:
            dic={}
            dic[0]=w0
            dic[1]=w1
            weight_combinations.append(dic)
            ratios.append(w0/w1)
weight_combinations
params = {'gamma': uniform(0,.5), 'learning_rate': uniform(.05,.25), 'max_depth': randint(3,7), 'reg_lambda': randint(1,10), 'subsample': uniform(.2,.7), 'scale_pos_weight':uniform(ratio-ratio/2,ratio)}

In [120]:
best_params = hyperparameter_optimizer(xgb_bin_0_1,param_grid=params,scoring='f1_weighted')
best_weights = weight_optimizer(weight_combinations,best_params=best_params)
improvement_threshold = 0.01  # Minimum improvement to continue optimization
previous_best_score = 0
ranking, best_f1_score, best_recall, best_precision = model_rating(params=best_params,weights=best_weights)
current_best_score = best_f1_score
for i in range(0,10):
    while current_best_score - previous_best_score > improvement_threshold:
        previous_best_score = current_best_score
        # Refine hyperparameters with current best weights
        best_params = hyperparameter_optimizer(xgb_bin_0_1,param_grid=params,scoring='f1_weighted',sample_weight=best_weights)

        # Refine weights with current best hyperparameters
        best_weights = best_weights = weight_optimizer(weight_combinations,best_params=best_params)

        # Evaluate the model with the new hyperparameters and weights
        ranking, best_f1_score, best_recall, best_precision = model_rating(params=best_params,weights=best_weights,ranking=ranking)
        current_best_score = best_f1_score
    # Final evaluation with the test set


Fitting 3 folds for each of 180 candidates, totalling 540 fits
[0]	validation_0-aucpr:0.59297
[1]	validation_0-aucpr:0.61157
[2]	validation_0-aucpr:0.64446
[3]	validation_0-aucpr:0.59762
[4]	validation_0-aucpr:0.61558
[5]	validation_0-aucpr:0.60049
[6]	validation_0-aucpr:0.61280
[7]	validation_0-aucpr:0.61992
[8]	validation_0-aucpr:0.60913
[9]	validation_0-aucpr:0.60718
[10]	validation_0-aucpr:0.61181
[11]	validation_0-aucpr:0.63915
[12]	validation_0-aucpr:0.63938
[13]	validation_0-aucpr:0.63310
[14]	validation_0-aucpr:0.63484
[15]	validation_0-aucpr:0.63527
[16]	validation_0-aucpr:0.62881
[17]	validation_0-aucpr:0.64601
[18]	validation_0-aucpr:0.64259
[19]	validation_0-aucpr:0.65233
[20]	validation_0-aucpr:0.65527
[21]	validation_0-aucpr:0.65077
[22]	validation_0-aucpr:0.65859
[23]	validation_0-aucpr:0.66265
[24]	validation_0-aucpr:0.66043
[25]	validation_0-aucpr:0.67067
[26]	validation_0-aucpr:0.67047
[27]	validation_0-aucpr:0.66805
[28]	validation_0-aucpr:0.66975
[29]	validation_0-a

c:\Users\p0pp1\miniconda3\Lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


[0]	validation_0-aucpr:0.60001
[1]	validation_0-aucpr:0.64699
[2]	validation_0-aucpr:0.64360
[3]	validation_0-aucpr:0.62910
[4]	validation_0-aucpr:0.62026
[5]	validation_0-aucpr:0.61753
[6]	validation_0-aucpr:0.61601
[7]	validation_0-aucpr:0.60494
[8]	validation_0-aucpr:0.60413
[9]	validation_0-aucpr:0.61674
[10]	validation_0-aucpr:0.61830
[11]	validation_0-aucpr:0.61667
[12]	validation_0-aucpr:0.65214
[13]	validation_0-aucpr:0.65583
[14]	validation_0-aucpr:0.65048
[15]	validation_0-aucpr:0.65722
[16]	validation_0-aucpr:0.66461
[17]	validation_0-aucpr:0.66898
[18]	validation_0-aucpr:0.66413
[19]	validation_0-aucpr:0.67431
[20]	validation_0-aucpr:0.66823
[21]	validation_0-aucpr:0.67433
[22]	validation_0-aucpr:0.68874
[23]	validation_0-aucpr:0.68201
[24]	validation_0-aucpr:0.68650
[25]	validation_0-aucpr:0.70105
[26]	validation_0-aucpr:0.69919
[27]	validation_0-aucpr:0.69677
[28]	validation_0-aucpr:0.69459
[29]	validation_0-aucpr:0.69316
[30]	validation_0-aucpr:0.69564
[31]	validation_0-

In [123]:
best_f1_score = sorted(ranking, key=lambda x: x['f1'], reverse=True)
best_recall = sorted(ranking, key=lambda x: x['recall'], reverse=True)
best_precision = sorted(ranking, key=lambda x: x['precision'], reverse=True)
print(best_precision[0]['full_report'])
model_01_p=best_precision[0]
print(best_recall[0]['full_report'])
model_01_r=best_recall[0]
print(best_f1_score[0]['full_report'])
model_01_f=best_f1_score[0]

              precision    recall  f1-score   support

           0       0.92      0.73      0.81       228
           1       0.64      0.88      0.74       127

    accuracy                           0.78       355
   macro avg       0.78      0.80      0.78       355
weighted avg       0.82      0.78      0.79       355

              precision    recall  f1-score   support

           0       0.92      0.73      0.81       228
           1       0.64      0.88      0.74       127

    accuracy                           0.78       355
   macro avg       0.78      0.80      0.78       355
weighted avg       0.82      0.78      0.79       355

              precision    recall  f1-score   support

           0       0.94      0.71      0.81       228
           1       0.64      0.91      0.75       127

    accuracy                           0.79       355
   macro avg       0.79      0.81      0.78       355
weighted avg       0.83      0.79      0.79       355



In [124]:
def opt(i):
    X=binary_datasets[i]['X_binary']
    y=binary_datasets[i]['y_binary']
    X_train,X_test,y_train,y_test=train_test_split(X,y,random_state=1,test_size=0.2, stratify=y)

    # Assuming y_train contains your training labels
    unique_classes, counts = np.unique(y_train, return_counts=True)
    class_counts = dict(zip(unique_classes, counts))

    # Calculate the ratio
    # For a binary classification (class 0 and class 1 for example)
    if len(class_counts) == 2:
        ratio = max(counts) / min(counts)
        print("Class Imbalance Ratio:", ratio)
    else:
        print("Class counts:", class_counts)
    # Define the SMOTE method
    smote = SMOTE()

    # Create the resampled feature set
    X_resampled, y_resampled = smote.fit_resample(X_train, y_train)
    base_params= {'eval_metric': 'aucpr', 'objective': 'binary:logistic', 'random_state': 1, 'device': 'cpu'}
    # create model
    xgb_bin_0_1=XGBClassifier(**base_params)
    xgb_bin_0_1.fit(X_resampled,y_resampled,verbose=True,eval_set=[(X_test,y_test)])
    #
    params = {'gamma': uniform(0,.5), 'learning_rate': uniform(.05,.25), 'max_depth': randint(3,7), 'reg_lambda': randint(1,10), 'subsample': uniform(.2,.7), 'scale_pos_weight':uniform(ratio-ratio/2,ratio)}
    best_params = hyperparameter_optimizer(xgb_bin_0_1,param_grid=params,scoring='f1_weighted')
    best_weights = weight_optimizer(weight_combinations,best_params=best_params)
    improvement_threshold = 0.01  # Minimum improvement to continue optimization
    previous_best_score = 0
    ranking, best_f1_score, best_recall, best_precision = model_rating(params=best_params,weights=best_weights)
    current_best_score = best_f1_score
    for i in range(0,10):
        while current_best_score - previous_best_score > improvement_threshold:
            previous_best_score = current_best_score
            # Refine hyperparameters with current best weights
            best_params = hyperparameter_optimizer(xgb_bin_0_1,param_grid=params,scoring='f1_weighted',sample_weight=best_weights)

            # Refine weights with current best hyperparameters
            best_weights = best_weights = weight_optimizer(weight_combinations,best_params=best_params)

            # Evaluate the model with the new hyperparameters and weights
            ranking, best_f1_score, best_recall, best_precision = model_rating(params=best_params,weights=best_weights,ranking=ranking)
            current_best_score = best_f1_score
        # Final evaluation with the test set
    best_f1_score = sorted(ranking, key=lambda x: x['f1'], reverse=True)
    best_recall = sorted(ranking, key=lambda x: x['recall'], reverse=True)
    best_precision = sorted(ranking, key=lambda x: x['precision'], reverse=True)
    print(best_precision[0]['full_report'])
    model_p=best_precision[0]
    print(best_recall[0]['full_report'])
    model_r=best_recall[0]
    print(best_f1_score[0]['full_report'])
    model_f=best_f1_score[0]
    return model_p, model_r, model_f

In [125]:
model_p_02, model_r_02, model_f_02=opt(1)
model_p_12, model_r_12, model_f_12=opt(2)

Class Imbalance Ratio: 1.5527472527472528
Fitting 3 folds for each of 180 candidates, totalling 540 fits
[0]	validation_0-aucpr:0.59925
[1]	validation_0-aucpr:0.60264
[2]	validation_0-aucpr:0.61463
[3]	validation_0-aucpr:0.61078
[4]	validation_0-aucpr:0.60230
[5]	validation_0-aucpr:0.60039
[6]	validation_0-aucpr:0.61143
[7]	validation_0-aucpr:0.60576
[8]	validation_0-aucpr:0.59716
[9]	validation_0-aucpr:0.61019
[10]	validation_0-aucpr:0.61658
[11]	validation_0-aucpr:0.63098
[12]	validation_0-aucpr:0.63568
[13]	validation_0-aucpr:0.63141
[14]	validation_0-aucpr:0.63940
[15]	validation_0-aucpr:0.64409
[16]	validation_0-aucpr:0.63420
[17]	validation_0-aucpr:0.65494
[18]	validation_0-aucpr:0.65078
[19]	validation_0-aucpr:0.64781
[20]	validation_0-aucpr:0.65185
[21]	validation_0-aucpr:0.65625
[22]	validation_0-aucpr:0.66667
[23]	validation_0-aucpr:0.67140
[24]	validation_0-aucpr:0.67011
[25]	validation_0-aucpr:0.66614
[26]	validation_0-aucpr:0.65827
[27]	validation_0-aucpr:0.65830
[28]	vali

In [126]:
ranking=[]
model_p_02, model_r_02, model_f_02=opt(1)

Class Imbalance Ratio: 1.5527472527472528
Fitting 3 folds for each of 180 candidates, totalling 540 fits
[0]	validation_0-aucpr:0.60352
[1]	validation_0-aucpr:0.60375
[2]	validation_0-aucpr:0.62600
[3]	validation_0-aucpr:0.62825
[4]	validation_0-aucpr:0.61994
[5]	validation_0-aucpr:0.61333
[6]	validation_0-aucpr:0.60741
[7]	validation_0-aucpr:0.58980
[8]	validation_0-aucpr:0.60248
[9]	validation_0-aucpr:0.63343
[10]	validation_0-aucpr:0.62972
[11]	validation_0-aucpr:0.63577
[12]	validation_0-aucpr:0.63323
[13]	validation_0-aucpr:0.64622
[14]	validation_0-aucpr:0.64975
[15]	validation_0-aucpr:0.65972
[16]	validation_0-aucpr:0.65743
[17]	validation_0-aucpr:0.65791
[18]	validation_0-aucpr:0.64937
[19]	validation_0-aucpr:0.64868
[20]	validation_0-aucpr:0.64958
[21]	validation_0-aucpr:0.64893
[22]	validation_0-aucpr:0.66326
[23]	validation_0-aucpr:0.64769
[24]	validation_0-aucpr:0.64631
[25]	validation_0-aucpr:0.65046
[26]	validation_0-aucpr:0.65722
[27]	validation_0-aucpr:0.66286
[28]	vali

In [127]:
ranking=[]
model_p_12, model_r_12, model_f_12=opt(2)

Class Imbalance Ratio: 2.781496062992126
Fitting 3 folds for each of 180 candidates, totalling 540 fits
[0]	validation_0-aucpr:0.59421
[1]	validation_0-aucpr:0.59443
[2]	validation_0-aucpr:0.61033
[3]	validation_0-aucpr:0.60313
[4]	validation_0-aucpr:0.60309
[5]	validation_0-aucpr:0.61173
[6]	validation_0-aucpr:0.62990
[7]	validation_0-aucpr:0.61898
[8]	validation_0-aucpr:0.61743
[9]	validation_0-aucpr:0.61322
[10]	validation_0-aucpr:0.61068
[11]	validation_0-aucpr:0.61278
[12]	validation_0-aucpr:0.61902
[13]	validation_0-aucpr:0.63506
[14]	validation_0-aucpr:0.63932
[15]	validation_0-aucpr:0.62375
[16]	validation_0-aucpr:0.62303
[17]	validation_0-aucpr:0.63600
[18]	validation_0-aucpr:0.63767
[19]	validation_0-aucpr:0.63440
[20]	validation_0-aucpr:0.63651
[21]	validation_0-aucpr:0.62616
[22]	validation_0-aucpr:0.63514
[23]	validation_0-aucpr:0.64082
[24]	validation_0-aucpr:0.63922
[25]	validation_0-aucpr:0.64184
[26]	validation_0-aucpr:0.63487
[27]	validation_0-aucpr:0.64172
[28]	valid

c:\Users\p0pp1\miniconda3\Lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


[0]	validation_0-aucpr:0.58254
[1]	validation_0-aucpr:0.60758
[2]	validation_0-aucpr:0.61627
[3]	validation_0-aucpr:0.60421
[4]	validation_0-aucpr:0.60371
[5]	validation_0-aucpr:0.59963
[6]	validation_0-aucpr:0.62709
[7]	validation_0-aucpr:0.61765
[8]	validation_0-aucpr:0.60787
[9]	validation_0-aucpr:0.60810
[10]	validation_0-aucpr:0.61267
[11]	validation_0-aucpr:0.63601
[12]	validation_0-aucpr:0.62323
[13]	validation_0-aucpr:0.62217
[14]	validation_0-aucpr:0.62389
[15]	validation_0-aucpr:0.61516
[16]	validation_0-aucpr:0.61566
[17]	validation_0-aucpr:0.61767
[18]	validation_0-aucpr:0.63107
[19]	validation_0-aucpr:0.62724
[20]	validation_0-aucpr:0.62752
[21]	validation_0-aucpr:0.62949
[22]	validation_0-aucpr:0.62959
[23]	validation_0-aucpr:0.63715
[24]	validation_0-aucpr:0.62876
[25]	validation_0-aucpr:0.62028
[26]	validation_0-aucpr:0.62105
[27]	validation_0-aucpr:0.61601
[28]	validation_0-aucpr:0.61408
[29]	validation_0-aucpr:0.61421
[30]	validation_0-aucpr:0.61389
[31]	validation_0-

c:\Users\p0pp1\miniconda3\Lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


[0]	validation_0-aucpr:0.59034
[1]	validation_0-aucpr:0.60388
[2]	validation_0-aucpr:0.60017
[3]	validation_0-aucpr:0.60267
[4]	validation_0-aucpr:0.60384
[5]	validation_0-aucpr:0.60757
[6]	validation_0-aucpr:0.62438
[7]	validation_0-aucpr:0.61683
[8]	validation_0-aucpr:0.60904
[9]	validation_0-aucpr:0.60690
[10]	validation_0-aucpr:0.60848
[11]	validation_0-aucpr:0.60477
[12]	validation_0-aucpr:0.59144
[13]	validation_0-aucpr:0.59072
[14]	validation_0-aucpr:0.58362
[15]	validation_0-aucpr:0.58478
[16]	validation_0-aucpr:0.58050
[17]	validation_0-aucpr:0.57501
[18]	validation_0-aucpr:0.57518
[19]	validation_0-aucpr:0.58015
[20]	validation_0-aucpr:0.58401
[21]	validation_0-aucpr:0.58574
[22]	validation_0-aucpr:0.59397
[23]	validation_0-aucpr:0.60158
[24]	validation_0-aucpr:0.60202
[25]	validation_0-aucpr:0.58931
[26]	validation_0-aucpr:0.59542


...

[0]	validation_0-aucpr:0.57319
[1]	validation_0-aucpr:0.62006
[2]	validation_0-aucpr:0.62249
[3]	validation_0-aucpr:0.61396
[4]	validation_0-aucpr:0.61418
[5]	validation_0-aucpr:0.62136
[6]	validation_0-aucpr:0.65017
[7]	validation_0-aucpr:0.64767
[8]	validation_0-aucpr:0.63262
[9]	validation_0-aucpr:0.63534
[10]	validation_0-aucpr:0.63299
[11]	validation_0-aucpr:0.64448
[12]	validation_0-aucpr:0.63404
[13]	validation_0-aucpr:0.63756
[14]	validation_0-aucpr:0.62981
[15]	validation_0-aucpr:0.62712
[16]	validation_0-aucpr:0.62797
[17]	validation_0-aucpr:0.63629
[18]	validation_0-aucpr:0.63622
[19]	validation_0-aucpr:0.63473
[20]	validation_0-aucpr:0.62952
[21]	validation_0-aucpr:0.65092
[22]	validation_0-aucpr:0.64902
[23]	validation_0-aucpr:0.64048
[24]	validation_0-aucpr:0.64212
[25]	validation_0-aucpr:0.63599
[26]	validation_0-aucpr:0.64114
[27]	validation_0-aucpr:0.64295
[28]	validation_0-aucpr:0.63772
[29]	validation_0-aucpr:0.63561
[30]	validation_0-aucpr:0.63589
[31]	validation_0-

c:\Users\p0pp1\miniconda3\Lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


[0]	validation_0-aucpr:0.56874
[1]	validation_0-aucpr:0.61942
[2]	validation_0-aucpr:0.64435
[3]	validation_0-aucpr:0.62180
[4]	validation_0-aucpr:0.61646
[5]	validation_0-aucpr:0.61939
[6]	validation_0-aucpr:0.62845
[7]	validation_0-aucpr:0.62602
[8]	validation_0-aucpr:0.61753
[9]	validation_0-aucpr:0.62260
[10]	validation_0-aucpr:0.62230
[11]	validation_0-aucpr:0.64902
[12]	validation_0-aucpr:0.63868
[13]	validation_0-aucpr:0.64484
[14]	validation_0-aucpr:0.62700
[15]	validation_0-aucpr:0.61693
[16]	validation_0-aucpr:0.62105
[17]	validation_0-aucpr:0.61952
[18]	validation_0-aucpr:0.62159
[19]	validation_0-aucpr:0.62539
[20]	validation_0-aucpr:0.61642
[21]	validation_0-aucpr:0.62117
[22]	validation_0-aucpr:0.62536
[23]	validation_0-aucpr:0.63312
[24]	validation_0-aucpr:0.63870
[25]	validation_0-aucpr:0.63701
[26]	validation_0-aucpr:0.64398
[27]	validation_0-aucpr:0.65428
[28]	validation_0-aucpr:0.64571
[29]	validation_0-aucpr:0.64132
[30]	validation_0-aucpr:0.64654
[31]	validation_0-

c:\Users\p0pp1\miniconda3\Lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


[0]	validation_0-aucpr:0.59541
[1]	validation_0-aucpr:0.65148
[2]	validation_0-aucpr:0.64505
[3]	validation_0-aucpr:0.62237
[4]	validation_0-aucpr:0.61701
[5]	validation_0-aucpr:0.61962
[6]	validation_0-aucpr:0.62883
[7]	validation_0-aucpr:0.62623
[8]	validation_0-aucpr:0.61747
[9]	validation_0-aucpr:0.62270
[10]	validation_0-aucpr:0.62691
[11]	validation_0-aucpr:0.65767
[12]	validation_0-aucpr:0.65834
[13]	validation_0-aucpr:0.67199
[14]	validation_0-aucpr:0.65038
[15]	validation_0-aucpr:0.63945
[16]	validation_0-aucpr:0.63996
[17]	validation_0-aucpr:0.64075
[18]	validation_0-aucpr:0.63820
[19]	validation_0-aucpr:0.64193
[20]	validation_0-aucpr:0.63315
[21]	validation_0-aucpr:0.62868
[22]	validation_0-aucpr:0.62951
[23]	validation_0-aucpr:0.64117
[24]	validation_0-aucpr:0.65184
[25]	validation_0-aucpr:0.64884
[26]	validation_0-aucpr:0.64932
[27]	validation_0-aucpr:0.65511
[28]	validation_0-aucpr:0.65746
[29]	validation_0-aucpr:0.65449
[30]	validation_0-aucpr:0.66075
[31]	validation_0-

# 02
The best f1:  {'id': 1, 'weights': {0: 1.3, 1: 1}, 'parameters': {'gamma': 0.24573828530788033, 'learning_rate': 0.20706825900495218, 'max_depth': 5, 'reg_lambda': 4, 'scale_pos_weight': 2.032450440780509, 'subsample': 0.8030762478717606, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7567567567567568, 'recall': 0.75, 'precision': 0.6627218934911243, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.92      0.75      0.83       228\n           1       0.66      0.88      0.76       127\n\n    accuracy                           0.80       355\n   macro avg       0.79      0.82      0.79       355\nweighted avg       0.83      0.80      0.80       355\n'}
The best recall:  {'id': 2, 'weights': {0: 0.4, 1: 0.3}, 'parameters': {'gamma': 0.44837395297324767, 'learning_rate': 0.18737481752622154, 'max_depth': 5, 'reg_lambda': 3, 'scale_pos_weight': 1.4396140391195817, 'subsample': 0.8356061255846248, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7509025270758124, 'recall': 0.7982456140350878, 'precision': 0.6933333333333334, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.89      0.80      0.84       228\n           1       0.69      0.82      0.75       127\n\n    accuracy                           0.81       355\n   macro avg       0.79      0.81      0.80       355\nweighted avg       0.82      0.81      0.81       355\n'}
The best precision:  {'id': 2, 'weights': {0: 0.4, 1: 0.3}, 'parameters': {'gamma': 0.44837395297324767, 'learning_rate': 0.18737481752622154, 'max_depth': 5, 'reg_lambda': 3, 'scale_pos_weight': 1.4396140391195817, 'subsample': 0.8356061255846248, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7509025270758124, 'recall': 0.7982456140350878, 'precision': 0.6933333333333334, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.89      0.80      0.84       228\n           1       0.69      0.82      0.75       127\n\n    accuracy                           0.81       355\n   macro avg       0.79      0.81      0.80       355\nweighted avg       0.82      0.81      0.81       355\n'}
### 02-2
The best f1:  {'id': 1, 'weights': {0: 1.3, 1: 1}, 'parameters': {'gamma': 0.13057464963398036, 'learning_rate': 0.2655380613377253, 'max_depth': 5, 'reg_lambda': 4, 'scale_pos_weight': 2.7997251971399377, 'subsample': 0.7026437946357962, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7466666666666667, 'recall': 0.7324561403508771, 'precision': 0.6473988439306358, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.92      0.73      0.81       228\n           1       0.65      0.88      0.75       127\n\n    accuracy                           0.79       355\n   macro avg       0.78      0.81      0.78       355\nweighted avg       0.82      0.79      0.79       355\n'}
The best recall:  {'id': 2, 'weights': {0: 1.5, 1: 1.8}, 'parameters': {'gamma': 0.05768422026941511, 'learning_rate': 0.28782763878381434, 'max_depth': 6, 'reg_lambda': 4, 'scale_pos_weight': 3.7343974412017835, 'subsample': 0.7514888945722058, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7465753424657535, 'recall': 0.7543859649122807, 'precision': 0.6606060606060606, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.91      0.75      0.82       228\n           1       0.66      0.86      0.75       127\n\n    accuracy                           0.79       355\n   macro avg       0.78      0.81      0.78       355\nweighted avg       0.82      0.79      0.80       355\n'}
The best precision:  {'id': 2, 'weights': {0: 1.5, 1: 1.8}, 'parameters': {'gamma': 0.05768422026941511, 'learning_rate': 0.28782763878381434, 'max_depth': 6, 'reg_lambda': 4, 'scale_pos_weight': 3.7343974412017835, 'subsample': 0.7514888945722058, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7465753424657535, 'recall': 0.7543859649122807, 'precision': 0.6606060606060606, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.91      0.75      0.82       228\n           1       0.66      0.86      0.75       127\n\n    accuracy                           0.79       355\n   macro avg       0.78      0.81      0.78       355\nweighted avg       0.82      0.79      0.80       355\n'}
 
# 12
The best f1:  {'id': 2, 'weights': {0: 1.1, 1: 0.6}, 'parameters': {'gamma': 0.35660000981612006, 'learning_rate': 0.19994268951018956, 'max_depth': 6, 'reg_lambda': 7, 'scale_pos_weight': 2.971848739671869, 'subsample': 0.874197266626825, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7508532423208191, 'recall': 0.7543859649122807, 'precision': 0.6626506024096386, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.91      0.75      0.82       228\n           1       0.66      0.87      0.75       127\n\n    accuracy                           0.79       355\n   macro avg       0.79      0.81      0.79       355\nweighted avg       0.82      0.79      0.80       355\n'}
The best recall:  {'id': 2, 'weights': {0: 1.1, 1: 0.6}, 'parameters': {'gamma': 0.35660000981612006, 'learning_rate': 0.19994268951018956, 'max_depth': 6, 'reg_lambda': 7, 'scale_pos_weight': 2.971848739671869, 'subsample': 0.874197266626825, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7508532423208191, 'recall': 0.7543859649122807, 'precision': 0.6626506024096386, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.91      0.75      0.82       228\n           1       0.66      0.87      0.75       127\n\n    accuracy                           0.79       355\n   macro avg       0.79      0.81      0.79       355\nweighted avg       0.82      0.79      0.80       355\n'}
The best precision:  {'id': 2, 'weights': {0: 1.1, 1: 0.6}, 'parameters': {'gamma': 0.35660000981612006, 'learning_rate': 0.19994268951018956, 'max_depth': 6, 'reg_lambda': 7, 'scale_pos_weight': 2.971848739671869, 'subsample': 0.874197266626825, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7508532423208191, 'recall': 0.7543859649122807, 'precision': 0.6626506024096386, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.91      0.75      0.82       228\n           1       0.66      0.87      0.75       127\n\n    accuracy                           0.79       355\n   macro avg       0.79      0.81      0.79       355\nweighted avg       0.82      0.79      0.80       355\n'}

# 01
The best f1:  {'id': 2, 'weights': {0: 1.1, 1: 1.3}, 'parameters': {'gamma': 0.060563183816341015, 'learning_rate': 0.1152912060617605, 'max_depth': 5, 'reg_lambda': 3, 'scale_pos_weight': 1.77496359894702, 'subsample': 0.8973897881580468, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.7532467532467533, 'recall': 0.7149122807017544, 'precision': 0.6408839779005525, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.94      0.71      0.81       228\n           1       0.64      0.91      0.75       127\n\n    accuracy                           0.79       355\n   macro avg       0.79      0.81      0.78       355\nweighted avg       0.83      0.79      0.79       355\n'}
The best recall:  {'id': 1, 'weights': {0: 0.7, 1: 0.8}, 'parameters': {'gamma': 0.07201052981648776, 'learning_rate': 0.13096661152235628, 'max_depth': 6, 'reg_lambda': 2, 'scale_pos_weight': 1.7101948621910785, 'subsample': 0.7278593647509122, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.744186046511628, 'recall': 0.7280701754385965, 'precision': 0.6436781609195402, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.92      0.73      0.81       228\n           1       0.64      0.88      0.74       127\n\n    accuracy                           0.78       355\n   macro avg       0.78      0.80      0.78       355\nweighted avg       0.82      0.78      0.79       355\n'}
The best precision:  {'id': 1, 'weights': {0: 0.7, 1: 0.8}, 'parameters': {'gamma': 0.07201052981648776, 'learning_rate': 0.13096661152235628, 'max_depth': 6, 'reg_lambda': 2, 'scale_pos_weight': 1.7101948621910785, 'subsample': 0.7278593647509122, 'eval_metric': 'aucpr', 'early_stopping_rounds': 20, 'objective': 'binary:logistic', 'random_state': 1}, 'f1': 0.744186046511628, 'recall': 0.7280701754385965, 'precision': 0.6436781609195402, 'full_report': '              precision    recall  f1-score   support\n\n           0       0.92      0.73      0.81       228\n           1       0.64      0.88      0.74       127\n\n    accuracy                           0.78       355\n   macro avg       0.78      0.80      0.78       355\nweighted avg       0.82      0.78      0.79       355\n'}


In [134]:
X=binary_datasets[2]['X_binary']
y=binary_datasets[2]['y_binary']
X_train,X_test,y_train,y_test=train_test_split(X,y,random_state=1,test_size=0.2, stratify=y)

# Assuming y_train contains your training labels
unique_classes, counts = np.unique(y_train, return_counts=True)
class_counts = dict(zip(unique_classes, counts))

# Calculate the ratio
# For a binary classification (class 0 and class 1 for example)
if len(class_counts) == 2:
    ratio = max(counts) / min(counts)
    print("Class Imbalance Ratio:", ratio)
    print("Class counts:", class_counts)

Class Imbalance Ratio: 2.781496062992126
Class counts: {0: 508, 1: 1413}


In [ ]:
{0:{0: 909, 1: 508}, 1:{0: 910, 1: 1413}, 2:{0: 508, 1: 1413}}